# 3.2 LOCATION QUOTIENT
 
**AUTOR: Fabrizio Ramirez Cutimbo**

**OBJETIVO**

- Aplicar técnicas de concentración regional para identificar indicios de Clusters Empresariales, en función de los ingresos de las empresas por provincias del Ecuador

In [1]:
# DATASET
import pandas as pd
import numpy as np

# GRÁFICOS
import matplotlib.pyplot as plt
import seaborn as sns

# MAPAS
import json
import folium

### Cargar Dataset

In [2]:
# Establecere formato de 2 decimales
pd.set_option('display.float_format', '{:.1f}'.format)
pd.set_option('display.max_colwidth', None) 

# Cargar dataset
pd_companias = pd.read_csv('Datasets Procesados/directorio_empresas_final_ciiu_completo.csv', dtype={'EXPEDIENTE': 'object', 'RUC': 'object'})

pd_companias.sample(1)

EXPEDIENTE            RUC SITUACION_LEGAL FECHA_CONSTITUCION     TIPO  \
13432      96986  1891733905001          ACTIVA         28/09/2009  ANÓNIMA   

          PAIS  REGION   PROVINCIA  CANTON             CIUDAD  ... SEGMENTO  \
13432  ECUADOR  SIERRA  TUNGURAHUA  AMBATO  JUAN BENIGNO VELA  ...  PEQUENA   

      IF_PRUEBA_ACIDA IF_ENDEUDAMIENTO_ACTIVO IF_APALANCAMIENTO  \
13432            23.5                     0.0               1.0   

      IF_ROTACION_VENTAS IF_MARGEN_BRUTO IF_MARGEN_OPERCIONAL IF_MARGEN_NETO  \
13432               25.7             1.0                  0.0            0.0   

       IF_ROE  IF_ROA  
13432     0.1     0.1  

[1 rows x 71 columns]

Se valida si existen valores nulos en las columnas de interes

In [3]:
pd_companias[['UTILIDAD_NETA_2023', 'INGRESOS_ACTIVIDADES_ORDINARIAS_2023']].isna().sum()

UTILIDAD_NETA_2023                      0
INGRESOS_ACTIVIDADES_ORDINARIAS_2023    0
dtype: int64

Se revisa medidas de tendencia central de las métricas UTILIDAD_NETA_2023 e INGRESOS_ACTIVIDADES_ORDINARIAS_2023

In [4]:
pd_companias[['UTILIDAD_NETA_2023', 'INGRESOS_ACTIVIDADES_ORDINARIAS_2023']].describe()

UTILIDAD_NETA_2023  INGRESOS_ACTIVIDADES_ORDINARIAS_2023
count             88673.0                               88673.0
mean              59741.0                             1714311.2
std             2043023.7                            20473081.7
min           -66586053.0                                   0.0
25%                   0.0                                9200.0
50%                   0.0                               80000.0
75%                1890.5                              404287.5
max           353861446.4                          2483015099.2

In [5]:
pd_companias.columns

Index(['EXPEDIENTE', 'RUC', 'SITUACION_LEGAL', 'FECHA_CONSTITUCION', 'TIPO',
       'PAIS', 'REGION', 'PROVINCIA', 'CANTON', 'CIUDAD', 'CIIU_NIVEL_1',
       'CIIU_NIVEL_1_DESC', 'CIIU_NIVEL_3', 'CIIU_NIVEL_3_DESC',
       'CIIU_NIVEL_4', 'CIIU_NIVEL_4_DESC', 'CIIU_NIVEL_6',
       'CIIU_NIVEL_6_DESC', 'ACTIVO_2022', 'ACTIVO_CORRIENTE_2022',
       'INVENTARIOS_2022', 'ACTIVOS_NO_CORRIENTES_2022', 'PASIVO_2022',
       'PASIVO_CORRIENTE_2022', 'PASIVO_NO_CORRIENTE_2022',
       'PATRIMONIO_NETO_2022', 'INGRESOS_ACTIVIDADES_ORDINARIAS_2022',
       'GANANCIA_BRUTA_2022', 'OTROS_INGRESOS_2022',
       'COSTO_VENTAS_PRODUCCION_2022', 'GASTOS_2022',
       'UTILIDAD_OPERATIVA_2022', 'GANACIA_PERDIDA_ANTES_IR_2022',
       'IMPUESTO_RENTA_2022', 'UTILIDAD_NETA_2022', 'ACTIVO_2023',
       'ACTIVO_CORRIENTE_2023', 'INVENTARIOS_2023',
       'ACTIVOS_NO_CORRIENTES_2023', 'PASIVO_2023', 'PASIVO_CORRIENTE_2023',
       'PASIVO_NO_CORRIENTE_2023', 'PATRIMONIO_NETO_2023',
       'INGRESOS_ACTIVID

## Función para cálculo de Location Quotient (LQ)

In [6]:
def calcular_location_quotient(dataset, metrica, provincia_col, cluster_col):
    """
    Calcula el Quotient Location (QL) para un dataset dado.

    Parámetros:
    - dataset: DataFrame de entrada que contiene los datos.
    - metrica: Columna que representa la métrica económica (e.g., Empleados UTILIDAD_NETA_2023).
    - provincia_col: Nombre de la columna que contiene las provincias (o región Menor).
    - cluster_col: Nombre de la columna que contiene los clusters (La Actividad Económica).

    Retorna:
    - DataFrame con columnas para provincia, cluster y el valor calculado de QL.
    """
    # Calcular totales por cluster y provincia
    # totales_clusters_provincias = dataset.groupby([provincia_col, cluster_col])[metrica].sum()
    totales_clusters_provincias = dataset.groupby([provincia_col, cluster_col])[metrica].agg(['sum', 'count']).reset_index()

    # Calcular totales por provincia
    totales_provincias = dataset.groupby(provincia_col)[metrica].sum()

    # Calcular totales por cluster a nivel nacional
    totales_clusters_nacional = dataset.groupby(cluster_col)[metrica].sum()

    # Calcular total nacional
    totales_nacional = dataset[metrica].sum()

    # Crear lista para almacenar los resultados
    lq_data = []
    
    for index, row in totales_clusters_provincias.iterrows():
        provincia = row[provincia_col]
        cluster = row[cluster_col]
        total_suma = row['sum']
        total_conteo = row['count']
        # Proporción del cluster dentro de la provincia
        proporcion_cluster_provincia = total_suma / totales_provincias[provincia]

        # Proporción del cluster a nivel nacional
        proporcion_cluster_region = totales_clusters_nacional[cluster] / totales_nacional

        # Se ha detectado que hay empresas que a pesar de tener ingresos no tienen resultados del ejercicio (utilidad, impuestos, etc)
        # Estos valores se establecen en 0, auqnue podrían establecerse en NaN para análisis futuros
        if proporcion_cluster_region == 0:
            lq = 0 # Si el Divisor es 0, no se realiza la división sino se establece directamente en 0
            
        else: 
            # Calcular QL
            lq = proporcion_cluster_provincia / proporcion_cluster_region

        # # Verificar si alguna proporción es un valor no numérico
        # if not np.isfinite(lq):
        #     print(f"Valor no numérico encontrado: {provincia} - {cluster}")
        #     print(f"Proporciones: {proporcion_cluster_provincia}, {proporcion_cluster_region}")
        #     lq = np.nan        

        # Agregar resultado a la lista
        lq_data.append({
            provincia_col: provincia,
            cluster_col: cluster,
            'Nro Empresas': total_conteo,
            'LQ': lq
        })

    # Convertir resultados a DataFrame
    lq_dataframe = pd.DataFrame(lq_data)

    # Ordenar por QL descendente
    lq_dataframe = lq_dataframe.sort_values(by='LQ', ascending=False)

    return lq_dataframe

#### Cálculo Manual del Location Quotient

In [7]:
metrica = 'INGRESOS_ACTIVIDADES_ORDINARIAS_2023'
col_ciiu_grupo = 'CIIU_NIVEL_4_DESC'
col_area_menor = 'PROVINCIA'

provincia_evaluada = 'CAÑAR'
ciiu_evaluada = 'TRANSPORTE DE CARGA POR CARRETERA'

# CIIU Por Provincia
totales_clusters_provincias = pd_companias.groupby([col_area_menor, col_ciiu_grupo])[metrica].agg(['sum', 'count']).reset_index()
a = totales_clusters_provincias[(totales_clusters_provincias[col_area_menor]==provincia_evaluada) & (totales_clusters_provincias[col_ciiu_grupo]==ciiu_evaluada)]['sum'].iloc[0]
print(a)

# Total Provincia
totales_provincias = pd_companias.groupby([col_area_menor])[metrica].agg(['sum', 'count']).reset_index()
b = totales_provincias[(totales_provincias[col_area_menor]==provincia_evaluada)]['sum'].iloc[0]
print(b)

# CIIU a nivel Nacional
totales_clusters = pd_companias.groupby([col_ciiu_grupo])[metrica].agg(['sum', 'count']).reset_index()
c = totales_clusters[(totales_clusters[col_ciiu_grupo]==ciiu_evaluada)]['sum'].iloc[0]
print(c)

# Total nacional
total_nacional = pd_companias[metrica].sum().round(2)
d = total_nacional
print(d)

# Cálculo LQ
print(f'Proporcion 1: {a/b}')
print(f'Proporcion 2: {c/d}')
print(f'LQ 1: {(a/b)/(c/d)}')

75710630.59
415425966.54
2796302387.08
152013115220.39
Proporcion 1: 0.18224819026258454
Proporcion 2: 0.018395139018274147
LQ 1: 9.90741032625712


## Identificación de Concentraciones (Clusters) por Location Quotient

### Experimento 1: Clusters por **Provincia** y por **Utilidad Neta**

**NOTA**, el Location Quotiente se creo inicialmente para utilizar como métrica el "Número de Empleados", es decir una métrica que solo puede ser positiva. No puede existir un número negativo de empleados, en este sentido, la utilidad Neta puede ser negativa si una empresa se encuentra en perdida, lo cual distorsiona el cálculo de proporciones.
De todos modos, se hace el cálculo para visualizar este potencial problema.

In [8]:
# Cálculo del Location Quotient por PROVINCIA y UTILIDAD_NETA_2023.
location_quotient_por_utilidad_neta = calcular_location_quotient(dataset=pd_companias, metrica='UTILIDAD_NETA_2023', provincia_col='PROVINCIA', cluster_col='CIIU_NIVEL_4_DESC')
print(location_quotient_por_utilidad_neta.shape)
location_quotient_por_utilidad_neta.head(3)

(3641, 4)


PROVINCIA  \
3039  SANTA ELENA   
425         CAÑAR   
422         CAÑAR   

                                                          CIIU_NIVEL_4_DESC  \
3039                 OTRAS ACTIVIDADES DE ASISTENCIA SOCIAL SIN ALOJAMIENTO   
425                                                   ELABORACIÓN DE AZÚCAR   
422   CULTIVO DE CEREALES (EXCEPTO ARROZ), LEGUMBRES Y SEMILLAS OLEAGINOSAS   

      Nro Empresas      LQ  
3039             1 46134.1  
425              1  9178.5  
422              3  6390.1

Selección de Clusters

+ Un cluster es una aglomeración de empresas en un espacio geográfico, se establece un número mínimo de "X" empresas (usualmente 20) para ser considerado cluster
+ El LQ calculado debe ser superior a un UMBRAL, usualmente 1.5
+ En este caso seremos más estrictos para poder


In [9]:
#Filtramos
numero_minimo_empresas = 50
lq_altamente_conentrado = 3
location_quotient_por_utilidad_neta = location_quotient_por_utilidad_neta[(location_quotient_por_utilidad_neta['Nro Empresas'] >= numero_minimo_empresas) & 
                                                                          (location_quotient_por_utilidad_neta['LQ'] >= lq_altamente_conentrado)  ]
print(location_quotient_por_utilidad_neta.shape)
location_quotient_por_utilidad_neta.head(5)

(49, 4)


PROVINCIA  \
462         CAÑAR   
1042   ESMERALDAS   
38          AZUAY   
3046  SANTA ELENA   
2628    PICHINCHA   

                                                   CIIU_NIVEL_4_DESC  \
462                                TRANSPORTE DE CARGA POR CARRETERA   
1042  OTRAS ACTIVIDADES DE TRANSPORTE DE PASAJEROS POR VÍA TERRESTRE   
38                           ACTIVIDADES DE PROGRAMACIÓN INFORMÁTICA   
3046  OTRAS ACTIVIDADES DE TRANSPORTE DE PASAJEROS POR VÍA TERRESTRE   
2628                         ACTIVIDADES DE PROGRAMACIÓN INFORMÁTICA   

      Nro Empresas    LQ  
462            174 681.3  
1042            54 396.2  
38              70 347.3  
3046            68 174.1  
2628           572 137.4

### **Experimento 2:** Clusters por **Provincia** y por **Ingresos 2023**

Interpretación más extendida:

+ LQ < 1: La provincia tiene Menor concentración relativa en esta industria que el promedio nacional. Posiblemente la industria es menos importante para la economía de la región.
+ LQ = 1: La provincia tiene concentración en esta industria equivalente al promedio nacional. Posiblemente la industria es menos importante para la economía de la región.
+ LQ > 1: La provincia tiene Mayor concentración relativa en esta industria que el promedio nacional. Posiblemente exista una especialización realtiva de la provincia en la industria.
+ 1 < LQ < 2: Concentración significativa; la industria comienza a ser considerada una parte clave de la economía local.
+ LQ > 2: Concentración Altamente Significativa podría indicar la existencia de un Cluster Industrial.


0 - 1: BAJA
1 - 1.5: MEDIA
1.5 - 2: ALTA
2 >: MUY ALTA

**NOTA**, Por el contrario, los "Ingresos" corresponden a una cuenta que existe en los numeros naturales positivos, similar al número de empleados. Se detecta números un tanto más realistas.

In [10]:
# Cálculo del Location Quotient por PROVINCIA y INGRESOS_ACTIVIDADES_ORDINARIAS_2023.
location_quotient_por_ingresos = calcular_location_quotient(dataset=pd_companias, metrica='INGRESOS_ACTIVIDADES_ORDINARIAS_2023', 
                                                            provincia_col='PROVINCIA', 
                                                            cluster_col='CIIU_NIVEL_4_DESC')
print(location_quotient_por_ingresos.shape)
location_quotient_por_ingresos.head(5)

(3641, 4)


PROVINCIA  \
3278   SUCUMBIOS   
548   CHIMBORAZO   
1155   GALAPAGOS   
1153   GALAPAGOS   
1637    IMBABURA   

                                                                      CIIU_NIVEL_4_DESC  \
3278  ACTIVIDADES DE CAMPAMENTOS, PARQUES DE VEHÍCULOS DE RECREO Y PARQUES DE CARAVANAS   
548                                               EXTRACCIÓN DE PIEDRA, ARENA Y ARCILLA   
1155                          TRANSPORTE DE PASAJEROS POR VÍAS DE NAVEGACIÓN INTERIORES   
1153                                     TRANSPORTE DE PASAJEROS MARÍTIMO Y DE CABOTAJE   
1637                                                  EXTRACCIÓN DE MINERALES DE HIERRO   

      Nro Empresas    LQ  
3278             1 400.9  
548              4 215.5  
1155             4 215.1  
1153            39 192.4  
1637             1 185.0

In [11]:
# Aplicación de Filtros
numero_minimo_empresas = 20
lq_altamente_conentrado = 4

location_quotient_por_ingresos = location_quotient_por_ingresos[(location_quotient_por_ingresos['Nro Empresas'] >= numero_minimo_empresas) & 
                                                                          (location_quotient_por_ingresos['LQ'] >= lq_altamente_conentrado)]
print(location_quotient_por_ingresos.shape)

location_quotient_por_ingresos = location_quotient_por_ingresos.sort_values(by=['PROVINCIA', 'LQ'], ascending=[True, False])

location_quotient_por_ingresos.head(50)


(59, 4)


PROVINCIA  \
277             AZUAY   
259             AZUAY   
144             AZUAY   
315           BOLIVAR   
375            CARCHI   
462             CAÑAR   
464             CAÑAR   
598        CHIMBORAZO   
504        CHIMBORAZO   
517        CHIMBORAZO   
577        CHIMBORAZO   
675          COTOPAXI   
756          COTOPAXI   
864            EL ORO   
842            EL ORO   
827            EL ORO   
1042       ESMERALDAS   
1063       ESMERALDAS   
1153        GALAPAGOS   
1100        GALAPAGOS   
1140        GALAPAGOS   
1089        GALAPAGOS   
1154        GALAPAGOS   
1090        GALAPAGOS   
1697         IMBABURA   
1588         IMBABURA   
1845             LOJA   
1773             LOJA   
1863             LOJA   
1936         LOS RIOS   
1942         LOS RIOS   
2011         LOS RIOS   
2016         LOS RIOS   
2212           MANABI   
2136           MANABI   
2321  MORONA SANTIAGO   
2304  MORONA SANTIAGO   
2329  MORONA SANTIAGO   
2368             NAPO   
2403             NAPO   
2369             NAPO   
2492         ORELLANA   
2418         ORELLANA   
2473         ORELLANA   
2539          PASTAZA   
2567          PASTAZA   
2540          PASTAZA   
3053      SANTA ELENA   
2945      SANTA ELENA   
2979      SANTA ELENA   

                                                                                                                                      CIIU_NIVEL_4_DESC  \
277                                                              VENTA, MANTENIMIENTO Y REPARACIÓN DE MOTOCICLETAS Y DE SUS PARTES, PIEZAS Y ACCESORIOS   
259   VENTA AL POR MENOR DE APARATOS ELÉCTRICOS DE USO DOMÉSTICO, MUEBLES, EQUIPO DE ILUMINACIÓN Y OTROS ENSERES DOMÉSTICOS EN COMERCIOS ESPECIALIZADOS   
144                                                                                                                              FABRICACIÓN DE MUEBLES   
315                                                                                                                   TRANSPORTE DE CARGA POR CARRETERA   
375                                                                                                                   TRANSPORTE DE CARGA POR CARRETERA   
462                                                                                                                   TRANSPORTE DE CARGA POR CARRETERA   
464                                                                                        TRANSPORTE URBANO Y SUBURBANO DE PASAJEROS POR VÍA TERRESTRE   
598                                                                                                                   TRANSPORTE DE CARGA POR CARRETERA   
504                                                                                                                    ACTIVIDADES DE SEGURIDAD PRIVADA   
517                                                                                                  CONSTRUCCIÓN DE CARRETERAS Y LÍNEAS DE FERROCARRIL   
577                                                                                      OTRAS ACTIVIDADES DE TRANSPORTE DE PASAJEROS POR VÍA TERRESTRE   
675                                                                                                                CULTIVO DE OTRAS PLANTAS NO PERENNES   
756                                                                                                                   TRANSPORTE DE CARGA POR CARRETERA   
864                                                                                               EXTRACCIÓN DE OTROS MINERALES METALÍFEROS NO FERROSOS   
842                                                                                                        CULTIVO DE FRUTAS TROPICALES Y SUBTROPICALES   
827                                                                                                                                  ACUICULTURA MARINA   
1042                                                                                     OTRAS ACTIVI

In [12]:
location_quotient_por_ingresos['CIIU_NIVEL_4_DESC'].unique()

array(['VENTA, MANTENIMIENTO Y REPARACIÓN DE MOTOCICLETAS Y DE SUS PARTES, PIEZAS Y ACCESORIOS',
       'VENTA AL POR MENOR DE APARATOS ELÉCTRICOS DE USO DOMÉSTICO, MUEBLES, EQUIPO DE ILUMINACIÓN Y OTROS ENSERES DOMÉSTICOS EN COMERCIOS ESPECIALIZADOS',
       'FABRICACIÓN DE MUEBLES', 'TRANSPORTE DE CARGA POR CARRETERA',
       'TRANSPORTE URBANO Y SUBURBANO DE PASAJEROS POR VÍA TERRESTRE',
       'ACTIVIDADES DE SEGURIDAD PRIVADA',
       'CONSTRUCCIÓN DE CARRETERAS Y LÍNEAS DE FERROCARRIL',
       'OTRAS ACTIVIDADES DE TRANSPORTE DE PASAJEROS POR VÍA TERRESTRE',
       'CULTIVO DE OTRAS PLANTAS NO PERENNES',
       'EXTRACCIÓN DE OTROS MINERALES METALÍFEROS NO FERROSOS',
       'CULTIVO DE FRUTAS TROPICALES Y SUBTROPICALES',
       'ACUICULTURA MARINA',
       'TRANSPORTE DE PASAJEROS MARÍTIMO Y DE CABOTAJE',
       'ACTIVIDADES DE OPERADORES TURÍSTICOS',
       'OTROS SERVICIOS DE RESERVAS Y ACTIVIDADES CONEXAS',
       'ACTIVIDADES DE AGENCIAS DE VIAJES',
       'TRANSPORTE DE PASA

Exportar tabla resumen

In [13]:
location_quotient_por_ingresos.to_csv('Datasets Procesados\\LQ\\Lista_LQ_CIIU_4_Ingresos_Provincias.csv', 
                                      index=False, 
                                      sep=';', 
                                      float_format='%.2f',
                                      encoding='utf-8-sig',
                                      decimal=',')

### Tabla de Resumen Experimento 2

In [14]:
# Realizamos el MERGE entre los dos datasets por las columnas 'Provincia' y 'CIIU_NIVEL_4_DESC'
merged_df = pd.merge(location_quotient_por_ingresos,
                     pd_companias[['RUC', 'PROVINCIA', 'CIIU_NIVEL_1', 'CIIU_NIVEL_1_DESC', 'CIIU_NIVEL_4', 'CIIU_NIVEL_4_DESC', 'CIIU_NIVEL_6_DESC', 
                                   'SEGMENTO', 'INGRESOS_ACTIVIDADES_ORDINARIAS_2023', 'UTILIDAD_NETA_2023']],                       
                     on=['PROVINCIA', 'CIIU_NIVEL_4_DESC'], 
                     how='inner')


grouped_df = merged_df.groupby(['PROVINCIA', 'CIIU_NIVEL_1', 'CIIU_NIVEL_1_DESC', 'CIIU_NIVEL_4', 'CIIU_NIVEL_4_DESC', 'Nro Empresas', 'LQ'], 
                               as_index=False)[['INGRESOS_ACTIVIDADES_ORDINARIAS_2023', 
                                                'UTILIDAD_NETA_2023']].mean()

grouped_df = grouped_df.rename(columns={'INGRESOS_ACTIVIDADES_ORDINARIAS_2023': 'INGRESOS PROMEDIO',
                                        'UTILIDAD_NETA_2023': 'UTILIDAD PROMEDIO'})

grouped_df.shape

# Iterar cada uno de los registros
for index, row in grouped_df.iterrows():

    # Filtrar por PROVINCIA y CIIU_NIVEL_4_DESC
    df_filtrado = pd_companias[(pd_companias['PROVINCIA'] == row['PROVINCIA']) & (pd_companias['CIIU_NIVEL_4_DESC'] == row['CIIU_NIVEL_4_DESC'])]
    total_empresas = df_filtrado.shape[0] # Total Filas

    # Agrupar por Segmento
    pd_segmento = df_filtrado.groupby(['PROVINCIA', 'CIIU_NIVEL_4_DESC', 'SEGMENTO']).size().reset_index(name='TOTAL')

    pd_segmento_micro = (pd_segmento[pd_segmento['SEGMENTO'] == 'MICRO']['TOTAL'].sum() * 100 / total_empresas).round(2)
    pd_segmento_pequena = (pd_segmento[pd_segmento['SEGMENTO'] == 'PEQUENA']['TOTAL'].sum() * 100 / total_empresas).round(2)
    pd_segmento_mediana = (pd_segmento[pd_segmento['SEGMENTO'] == 'MEDIANA']['TOTAL'].sum() * 100 / total_empresas).round(2)
    pd_segmento_grande = (pd_segmento[pd_segmento['SEGMENTO'] == 'GRANDE']['TOTAL'].sum() * 100 / total_empresas).round(2)

    # Concatenamos los resultados de cada segmento con saltos de línea
    segment_distribution = (f"Micro: {pd_segmento_micro}% "
                            f"Pequeña: {pd_segmento_pequena}% "
                            f"Mediana: {pd_segmento_mediana}% "
                            f"Grande: {pd_segmento_grande}% ")
    
    # Añadir la columna "Distribución SEGMENTO" al dataframe
    grouped_df.loc[index, 'Distribución SEGMENTO'] = segment_distribution

    # # Agrupar por CIIU_NIVEL_6_DESC
    pd_ciiu_detalle = df_filtrado.groupby(['PROVINCIA', 'CIIU_NIVEL_4_DESC', 'CIIU_NIVEL_6_DESC']).size().reset_index(name='TOTAL')

    # Concatenar los valores de 'CIIU_NIVEL_6_DESC' con el 'TOTAL' y separarlos por comas
    ciiu_detalle_concat = pd_ciiu_detalle.apply(lambda x: f"{x['CIIU_NIVEL_6_DESC']} ({x['TOTAL']})", axis=1).tolist()
    
    # Unir todos los valores con comas
    ciiu_detalle_string = ", ".join(ciiu_detalle_concat)

    # Añadir la columna "CIIU_NIVEL_6_DESC_lista" al dataframe
    grouped_df.loc[index, 'CIIU_NIVEL_6_DESC_lista'] = ciiu_detalle_string

   
    # print(pd_ciiu_detalle[['CIIU_NIVEL_6_DESC', 'TOTAL']])

# Formato Dolares
grouped_df['INGRESOS PROMEDIO'] = grouped_df['INGRESOS PROMEDIO'].apply(lambda x: f"${x:,.1f}")
grouped_df['UTILIDAD PROMEDIO'] = grouped_df['UTILIDAD PROMEDIO'].apply(lambda x: f"${x:,.1f}")


grouped_df.head(3)


PROVINCIA CIIU_NIVEL_1  \
0     AZUAY            C   
1     AZUAY            G   
2     AZUAY            G   

                                                                         CIIU_NIVEL_1_DESC  \
0                                                                INDUSTRIAS MANUFACTURERAS   
1  COMERCIO AL POR MAYOR Y AL POR MENOR REPARACIÓN DE VEHÍCULOS AUTOMOTORES Y MOTOCICLETAS   
2  COMERCIO AL POR MAYOR Y AL POR MENOR REPARACIÓN DE VEHÍCULOS AUTOMOTORES Y MOTOCICLETAS   

  CIIU_NIVEL_4  \
0        C3100   
1        G4540   
2        G4759   

                                                                                                                                   CIIU_NIVEL_4_DESC  \
0                                                                                                                             FABRICACIÓN DE MUEBLES   
1                                                             VENTA, MANTENIMIENTO Y REPARACIÓN DE MOTOCICLETAS Y DE SUS PARTES, PIEZAS Y ACCESORIOS   
2  VENTA AL POR MENOR DE APARATOS ELÉCTRICOS DE USO DOMÉSTICO, MUEBLES, EQUIPO DE ILUMINACIÓN Y OTROS ENSERES DOMÉSTICOS EN COMERCIOS ESPECIALIZADOS   

   Nro Empresas  LQ INGRESOS PROMEDIO UTILIDAD PROMEDIO  \
0            22 4.5      $1,956,526.1         $35,402.7   
1            40 9.4      $5,852,828.3         $11,432.6   
2            21 5.3      $7,835,470.4         $25,869.4   

                                           Distribución SEGMENTO  \
0  Micro: 45.45% Pequeña: 22.73% Mediana: 18.18% Grande: 13.64%    
1      Micro: 17.5% Pequeña: 47.5% Mediana: 17.5% Grande: 17.5%    
2  Micro: 19.05% Pequeña: 33.33% Mediana: 28.57% Grande: 19.05%    

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        CIIU_NIVEL_6_DESC_lista  
0  FABRICACIÓN DE MUEBLES DE MADERA Y SUS PARTES: PARA EL HOGAR, OFICINAS, TALLERES, HOTELES, RESTAURANTES, IGLESIAS, ESCUELAS, MUEBLES ESPECIALES PARA LOCALES COMERCIALES, MUEBLES PARA MÁQUINAS DE COSER, TELEVISIONES, ETCÉTERA (17), FABRICACIÓN DE MUEBLES DE METAL Y SUS PARTES: PARA EL HOGAR, OFICINA, TALLERES, HOTELES, RESTAURANTES, IGLESIAS, ESCUELAS, MUEBLES ESPECIALES PARA LOCALES COMERCIALES Y OTROS USOS (2), SERVICIOS DE APOYO A LA FABRICACIÓN Y ACABADO (TAPIZADO DE SILLAS Y SILLONES, LACADO, PINTADO, BARNIZADO CON MUÑEQUILLA, ETCÉTERA) DE MUEBLES A CAMBIO DE UNA RETRIBUCIÓN O POR CONTRATO (3)  
1                                                                                                                                                                                                                                                                                                                                                                                                                            VENTA DE MOTOCICLETAS, INCLUSO CICLOMOTORES (VELOMOTORES), TRICIMOTOS (31), VENTA DE PARTES, PIEZAS Y ACCESORIOS PARA MOTOCICLETAS (INCLUSO POR COMISIONISTAS Y COMPAÑÍAS DE VENTA POR CORREO) (9)  
2                                                                                                                                                                                                         VENTA AL POR MENOR DE ELECTRODOMÉSTICOS EN ESTABLECIMIENTOS ESPECIALIZADOS: REFRIGERADORAS, COCINAS, MICROONDAS, ETCÉTERA (9), VENTA AL POR MENOR DE MUEBLES DE USO DOMÉSTICO, COLCHONES Y SOMIERES EN ESTABLECIMIENTOS ESPECIALIZADOS (7), VENTA AL POR MENOR DE UTENSILIOS DE USO DOMÉSTICO, C

In [15]:
grouped_df['CIIU_NIVEL_4_DESC'] = grouped_df['CIIU_NIVEL_4_DESC'].str.capitalize()
grouped_df['PROVINCIA'] = grouped_df['PROVINCIA'].str.capitalize()

In [16]:
grouped_df.to_csv('Datasets Procesados\\LQ\\Tabla_Resumen_LQ_CIIU_4_Ingresos_Provincias.csv', 
                                      index=False, 
                                      sep=';', 
                                      float_format='%.2f',
                                      encoding='utf-8-sig',
                                      decimal=',')


## Visualización Geográfica

### Enriquecer dataset para Visualizar en MAPA

Se combina el dataset principal y el listado de aglomeraciones (LQ)

In [17]:

merged_df_for_map = pd.merge(pd_companias[['PROVINCIA', 'CIIU_NIVEL_1_DESC', 'CIIU_NIVEL_4_DESC', 'CIIU_NIVEL_6_DESC', 'SEGMENTO', 'CANTON']],                       
                                location_quotient_por_ingresos,
                                on=['PROVINCIA', 'CIIU_NIVEL_4_DESC'], 
                                how='inner')
# merged_df.head(5)
merged_df_for_map.head(1)

PROVINCIA  \
0  TUNGURAHUA   

                                                                         CIIU_NIVEL_1_DESC  \
0  COMERCIO AL POR MAYOR Y AL POR MENOR REPARACIÓN DE VEHÍCULOS AUTOMOTORES Y MOTOCICLETAS   

                CIIU_NIVEL_4_DESC  \
0  VENTA DE VEHÍCULOS AUTOMOTORES   

                                                                                                                                                                                                                                                                                                                           CIIU_NIVEL_6_DESC  \
0  VENTA DE VEHÍCULOS NUEVOS Y USADOS: VEHÍCULOS DE PASAJEROS, INCLUIDOS VEHÍCULOS ESPECIALIZADOS COMO: AMBULANCIAS Y MINIBUSES, CAMIONES, REMOLQUES Y SEMIRREMOLQUES, VEHÍCULOS DE ACAMPADA COMO: CARAVANAS Y AUTOCARAVANAS, VEHÍCULOS PARA TODO TERRENO (JEEPS, ETCÉTERA), INCLUIDO LA VENTA AL POR MAYOR Y AL POR MENOR POR COMISIONISTAS   

  SEGMENTO  CANTON  Nro Empresas  LQ  
0   GRANDE  AMBATO            30 6.6

### Generación dataset de Cantones con coordenadas geográficas

In [18]:
# Procesar json con Coordenadas de CANTONES de Ecuador
# Función para reemplazar las vocales con tilde por las correspondientes sin tilde
def reemplazar_vocales_tilde(texto):
    reemplazos = {
        'Á': 'A', 'É': 'E', 'Í': 'I', 'Ó': 'O', 'Ú': 'U',
        'á': 'a', 'é': 'e', 'í': 'i', 'ó': 'o', 'ú': 'u'
    }
    for vocal_con_tilde, vocal_sin_tilde in reemplazos.items():
        texto = texto.replace(vocal_con_tilde, vocal_sin_tilde)
    return texto

# Cargar el archivo JSON
with open('Utilitarios/CantonesDeEcuador.json', 'r', encoding='utf-8') as file:
    data = json.load(file)

# Crear una lista para almacenar los datos procesados
processed_data = []

# Iterar sobre los elementos del JSON
for canton in data:
    nombre_canton = canton['name'].upper()  # Convertir el nombre del cantón a mayúsculas
    nombre_canton = reemplazar_vocales_tilde(nombre_canton)  # Reemplazar vocales con tilde
    latitud = canton['latlng'][0]  # Latitud
    longitud = canton['latlng'][1]  # Longitud
    
    # Agregar los datos procesados a la lista
    processed_data.append({
        'CANTON': nombre_canton,
        'LATITUD': latitud,
        'LONGITUD': longitud
    })

# Crear un DataFrame de pandas
df = pd.DataFrame(processed_data)

# Guardar el DataFrame en un archivo CSV
df.to_csv('Utilitarios/cantones_latitudes_longitudes.csv', index=False, encoding='utf-8')

print("Archivo CSV generado correctamente.")

Archivo CSV generado correctamente.


Se carga el archivo csv con coordenadas de cantones

In [19]:
pd_cantones = pd.read_csv('Utilitarios/cantones_latitudes_longitudes.csv', encoding='utf-8')
pd_cantones.sample(5)

CANTON  LATITUD  LONGITUD
127   SAN JUAN BOSCO     -3.1     -78.5
85           LA MANA     -0.8     -79.1
67              MERA     -1.4     -78.1
45   OLMEDO (MANABI)     -1.4     -80.2
140      SAMBORONDON     -2.0     -79.7

In [20]:
# merged_df_for_map['CANTON'] = merged_df_for_map['CANTON'].replace('RUMINAHUI', 'RUMIÑAHUI')
# merged_df_for_map['CANTON'] = merged_df_for_map['CANTON'].replace('PABLO VI', 'PABLO SEXTO')

# merged_df_for_map.loc[merged_df_for_map['PROVINCIA'] == 'CARCHI', 'CANTON'] = merged_df_for_map.loc[merged_df_for_map['PROVINCIA'] == 'CARCHI', 'CANTON'].replace('BOLIVAR', 'BOLIVAR (CARCHI)')
# merged_df_for_map.loc[merged_df_for_map['PROVINCIA'] == 'MANABI', 'CANTON'] = merged_df_for_map.loc[merged_df_for_map['PROVINCIA'] == 'MANABI', 'CANTON'].replace('BOLIVAR', 'BOLIVAR (MANABI)')

# merged_df_for_map.loc[merged_df_for_map['PROVINCIA'] == 'LOJA', 'CANTON'] = merged_df_for_map.loc[merged_df_for_map['PROVINCIA'] == 'LOJA', 'CANTON'].replace('OLMEDO', 'OLMEDO (LOJA)')
# merged_df_for_map.loc[merged_df_for_map['PROVINCIA'] == 'MANABI', 'CANTON'] = merged_df_for_map.loc[merged_df_for_map['PROVINCIA'] == 'MANABI', 'CANTON'].replace('OLMEDO', 'OLMEDO (MANABI)')

Se enriquece el dataset "merged_df_for_map" con datos de geográficos de los cantones

In [21]:
# Realizamos el MERGE entre los dos datasets por la columna 'Canton'
merged_df_for_map = pd.merge(merged_df_for_map,                       
                             pd_cantones,
                             on=['CANTON'], 
                             how='left')

In [22]:
merged_df_for_map.shape

(3830, 10)

In [23]:
merged_df_for_map[merged_df_for_map['LATITUD'].isna()].head(5)

Empty DataFrame
Columns: [PROVINCIA, CIIU_NIVEL_1_DESC, CIIU_NIVEL_4_DESC, CIIU_NIVEL_6_DESC, SEGMENTO, CANTON, Nro Empresas, LQ, LATITUD, LONGITUD]
Index: []

In [24]:
merged_df_for_map.head(2)

PROVINCIA  \
0  TUNGURAHUA   
1      MANABI   

                                                                         CIIU_NIVEL_1_DESC  \
0  COMERCIO AL POR MAYOR Y AL POR MENOR REPARACIÓN DE VEHÍCULOS AUTOMOTORES Y MOTOCICLETAS   
1                                                                INDUSTRIAS MANUFACTURERAS   

                                               CIIU_NIVEL_4_DESC  \
0                                 VENTA DE VEHÍCULOS AUTOMOTORES   
1  ELABORACIÓN Y CONSERVACIÓN DE PESCADOS, CRUSTÁCEOS Y MOLUSCOS   

                                                                                                                                                                                                                                                                                                                           CIIU_NIVEL_6_DESC  \
0  VENTA DE VEHÍCULOS NUEVOS Y USADOS: VEHÍCULOS DE PASAJEROS, INCLUIDOS VEHÍCULOS ESPECIALIZADOS COMO: AMBULANCIAS Y MINIBUSES, CAMIONES, REMOLQUES Y SEMIRREMOLQUES, VEHÍCULOS DE ACAMPADA COMO: CARAVANAS Y AUTOCARAVANAS, VEHÍCULOS PARA TODO TERRENO (JEEPS, ETCÉTERA), INCLUIDO LA VENTA AL POR MAYOR Y AL POR MENOR POR COMISIONISTAS   
1                                                                                                                              PREPARACIÓN Y CONSERVACIÓN DE PESCADO, CRUSTÁCEOS (EXCEPTO CAMARÓN Y LANGOSTINOS) Y OTROS MOLUSCOS MEDIANTE EL CONGELADO, ULTRACONGELADO, SECADO, AHUMADO, SALADO, SUMERGIDO EN SALMUERA Y ENLATADO, ETCÉTERA   

  SEGMENTO  CANTON  Nro Empresas   LQ  LATITUD  LONGITUD  
0   GRANDE  AMBATO            30  6.6     -1.2     -78.6  
1   GRANDE   MANTA            44 11.7     -1.0     -80.8

In [25]:
merged_df_for_map['CIIU_NIVEL_4_DESC'] = merged_df_for_map['CIIU_NIVEL_4_DESC'].str.capitalize()
merged_df_for_map['PROVINCIA'] = merged_df_for_map['PROVINCIA'].str.capitalize()


In [26]:
merged_df_for_map.to_csv('Datasets Procesados\\LQ\\Tabla_Mapa_LQ_CIIU_4_Ingresos_Provincias.csv', 
                                      index=False, 
                                      sep=';', 
                                      float_format='%.2f',
                                      encoding='utf-8-sig',
                                      decimal=',')

## Generación de un MAPA

https://python-visualization.github.io/folium/latest/user_guide/ui_elements/icons.html


In [27]:
merged_df_for_map[merged_df_for_map['LATITUD'].isna()]

Empty DataFrame
Columns: [PROVINCIA, CIIU_NIVEL_1_DESC, CIIU_NIVEL_4_DESC, CIIU_NIVEL_6_DESC, SEGMENTO, CANTON, Nro Empresas, LQ, LATITUD, LONGITUD]
Index: []

+ OpenStreetMap: tiles='OpenStreetMap' (predeterminado, mapa simple)
+ Stamen Terrain: tiles='Stamen Terrain' (mapa con relieve)
+ Stamen Toner: tiles='Stamen Toner' (mapa en blanco y negro)
+ CartoDB positron: tiles='CartoDB positron' (estilo limpio y claro)
+ CartoDB dark_matter: tiles='CartoDB dark_matter' (mapa oscuro)

In [28]:
categorias_unicas = merged_df_for_map['CIIU_NIVEL_4_DESC'].unique()
categorias_unicas

array(['Venta de vehículos automotores',
       'Elaboración y conservación de pescados, crustáceos y moluscos',
       'Transporte urbano y suburbano de pasajeros por vía terrestre',
       'Fabricación de prendas de vestir, excepto prendas de piel',
       'Transporte de carga por carretera',
       'Actividades de agencias de viajes',
       'Cultivo de productos agrícolas en combinación con la cría de animales (explotación mixta)',
       'Construcción de carreteras y líneas de ferrocarril',
       'Otras actividades de transporte de pasajeros por vía terrestre',
       'Cultivo de frutas tropicales y subtropicales',
       'Transporte de pasajeros por vía aérea',
       'Transporte de pasajeros marítimo y de cabotaje',
       'Acuicultura marina', 'Fabricación de muebles',
       'Venta al por menor de aparatos eléctricos de uso doméstico, muebles, equipo de iluminación y otros enseres domésticos en comercios especializados',
       'Construcción de proyectos de servicios públicos

In [29]:
# Función para convertir el color RGBA a hexadecimal
def rgba_to_hex(rgba):
    return '#{:02x}{:02x}{:02x}'.format(int(rgba[0] * 255), int(rgba[1] * 255), int(rgba[2] * 255))

# Crear un mapa centrado en Ecuador
mapa = folium.Map(location=[-1.8312, -78.1834], zoom_start=6, tiles='CartoDB positron')  # Centrado en Ecuador

# Obtener las categorías únicas de 'CIIU_NIVEL_1_DESC'
categorias_unicas = merged_df_for_map['CIIU_NIVEL_4_DESC'].unique()

# Crear una paleta de colores utilizando el nuevo acceso a los mapas de colores
colormap = plt.colormaps['tab20']  # Usando la nueva sintaxis para acceder a colormaps
colores = {categoria: colormap(i / len(categorias_unicas)) for i, categoria in enumerate(categorias_unicas)}

# Añadir marcadores para cada ciudad
for index, row in merged_df_for_map.iterrows():
    categoria = row['CIIU_NIVEL_4_DESC']
    color = colores.get(categoria, 'gray')  # Usar color gris si la categoría no está en el diccionario
    hex_color = rgba_to_hex(color)

    folium.CircleMarker(
        location=[row['LATITUD'], row['LONGITUD']],
        radius=5,  # Tamaño del círculo
        color=hex_color,  # Color del borde
        stroke=False,
        fill=True,
        fill_color=hex_color,  # Color de relleno
        fill_opacity=0.2,  # Opacidad del relleno
        popup=f'{categoria} y {row["CANTON"]}',  # Popup con el valor de CIIU_NIVEL_3_DESC
        tooltip=categoria  # Tooltip con el valor de CIIU_NIVEL_3_DESC
    ).add_to(mapa)

# Crear la leyenda HTML
legend_html = '''
<div style="position: fixed; 
            bottom: 50px; left: 50px; width: 200px; height: 300px; 
            border:2px solid grey; z-index:9999; font-size:10px;
            background-color:white; opacity: 0.8;">
    <h4 style="margin: 10px;">Categorías</h4>
    <ul style="list-style: none; padding: 0; margin: 0;">
'''
for categoria, color in colores.items():
    hex_color = rgba_to_hex(color)
    legend_html += f'<li style="margin: 5px;"><span style="background-color:{hex_color}; width: 20px; height: 20px; display: inline-block;"></span> {categoria}</li>'

legend_html += '''
    </ul>
</div>
'''

# Añadir la leyenda al mapa
# mapa.get_root().html.add_child(folium.Element(legend_html))

# Guardar el mapa
mapa.save("mapa_ciudades_categoria.html")

# Mostrar el mapa (en Jupyter, por ejemplo, puedes usar mapa)
mapa

In [30]:
# Suponiendo que merged_df_for_map ya está cargado y contiene LATITUD, LONGITUD y PROVINCIA

# Agrupar por coordenadas para calcular la densidad de puntos
densidad_puntos = merged_df_for_map.groupby(['LATITUD', 'LONGITUD']).size().reset_index(name='conteo')

# Normalizar los conteos para ajustar los radios
densidad_puntos['radio'] = densidad_puntos['conteo'] / densidad_puntos['conteo'].max() * 20  # Escalar radios (ajustar 20 según sea necesario)

# Crear el mapa
mapa = folium.Map(location=[-1.8312, -78.1834], zoom_start=6, tiles='CartoDB positron')

# Añadir círculos dinámicos al mapa
for _, row in densidad_puntos.iterrows():
    folium.CircleMarker(
        location=[row['LATITUD'], row['LONGITUD']],
        radius=row['radio'],  # Radio ajustado por la densidad
        color='blue',
        fill=True,
        fill_color='blue',
        fill_opacity=0.6,
        popup=f"Conteo: {row['conteo']}",  # Mostrar el número de puntos en el popup
        tooltip=f"Densidad: {row['conteo']}"
    ).add_to(mapa)

# Guardar el mapa
mapa.save("mapa_densidad_circulos.html")

# Mostrar el mapa (en Jupyter, por ejemplo, puedes usar mapa)
mapa